In [1]:
import math

import robin_stocks.robinhood as rh
import datetime as dt
import time
import pandas as pd
import requests
import matplotlib.pyplot as plt
import numpy as np
username ='markliang@yahoo.com'
password ='Jml168168$'


from datetime import datetime as dt
import datetime
today = dt.today()
a = str(today.year)
b = str(today.month)
c = str(today.day)
  
#
def login():
    rh.login(username, password)

login()


while(True):
    def get_stop(stock):    # pivotpoints
        from datetime import datetime as dt
        import datetime
        import dateutil
        today = datetime.datetime.today()
        delta = dateutil.relativedelta.relativedelta(months=1)
        end = ( today-datetime.timedelta(1)).strftime('%Y-%m-%d') 
        start = (today - delta).strftime('%Y-%m-%d')

        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{ticker}?from={start}&to={end}&apikey={api_key}').json()['historical']
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        last_day = stock.iloc[-1].to_frame().T
        not_pivots = last_day.columns
        last_day['center_gravity'] = (last_day['High'] + last_day['Low'] + last_day['Close'])/3
        last_day['vol_up1'] = 2*last_day['center_gravity'] - last_day['Low']
        last_day['vol_down1'] = 2*last_day['center_gravity'] - last_day['High']
        last_day['vol_up2'] = last_day['center_gravity'] + (last_day['High'] - last_day['Low'])
        last_day['vol_down2'] = last_day['center_gravity'] - (last_day['High'] - last_day['Low'])
        last_day['vol_up3'] = last_day['center_gravity'] + 2*(last_day['High'] - last_day['Low'])
        last_day['vol_down3'] = last_day['center_gravity'] - 2*(last_day['High'] - last_day['Low'])
        tick = ticker
        last_day.index = [tick]
        last_day['stop_loss'] = (last_day['vol_down2'] +last_day['vol_down3'] )/2
        last_day['stop_loss_pct'] = (last_day['Close']- last_day['stop_loss'])/last_day['Close']*100
        if last_day['stop_loss_pct'][-1] >3.5:
            last_day['stop_loss'][-1]= (last_day['vol_down1'][-1] +last_day['Close'][-1] )/2

        return last_day


    my_stocks = rh.build_holdings()
    df =pd.DataFrame(my_stocks).T
    df1 =df[['price','quantity','average_buy_price','percent_change']]

    stock = df1.index.tolist()
    all_data = pd.DataFrame()
    for  ticker in stock:
        print(ticker)
        last_day = get_stop(ticker)
        all_data = pd.concat([all_data,last_day], axis= 0)

    all_data = all_data[['stop_loss']]    
    all_data1 = df1.merge(all_data, left_index = True, right_index = True)
    all_data1['price'] = all_data1['price'].astype(float)
    all_data1['pct_cha'] = ((all_data1['price']-all_data1['stop_loss'])/ all_data1['price'] )*100
    import random
    x = random.random()
    y =float((x+5)/100)
    z =float( (10-x)/100)
    all_data1['average_buy_price'] = all_data1['average_buy_price'].astype(float)
    all_data1['target_price1'] = all_data1['average_buy_price'] *(1+y)
    all_data1['target_price2'] = all_data1['average_buy_price'] *(1+z)

    # 开始修改的部分

    # ...


    for s in all_data1.index.tolist():
        print(s)
        quantity = float(all_data1['quantity'][s])  # convert quantity to float once

        if all_data1['price'][s] < all_data1['stop_loss'][s]:
            rh.orders.order(symbol=s, quantity=quantity, side='sell', timeInForce='gtc')

            print(f"Stop loss order triggered for {s}, selling at market price.")

        if all_data1['price'][s] >= all_data1['target_price1'][s]:
            quantity1 = math.ceil(quantity / 2)  # sell half, round down to nearest integer
            rh.orders.order(symbol=s, quantity=quantity1, side='sell', timeInForce='gtc')

            print(f"First target price reached for {s}, selling half at market price.")

        if all_data1['price'][s] >= all_data1['target_price2'][s]:
            rh.orders.order(symbol=s, quantity=quantity, side='sell', timeInForce='gtc')

            print(f"Second target price reached for {s}, selling all at market price.")


    time.sleep(3600)
    


CSGP
ITRI
APD
CVX
CHTR
DOX
NXST
SGEN
ADC
EA
HOLX
MKC
HLI
TW
ARCH
BR
INTU
HUBG
BAX
FCN
GD
INCY
AAON
FIX
PNR
DHI
ALLE
BYD
HCA
MATX
MDLZ
MDT
EOG
FIVE
BURL
MNST
MAR
MSTR
NBIX
HHC
HLT
NVDA
SYY
ISRG
MSI
FND
ALNY
CHD
BRO
VRSN
AJG
GGG
ATVI
WFRD
ARGX
PXD
CL
IRDM
CTSH
TJX
EDU
MLI
NWE
CIVI
BNS
AZTA
SEAS
SHW
VEEV
AZN
ROST
XLV
ZBH
EXPD
GNRC
AXON
BCE
CMCSA
PODD
CHRD
FSV
HES
CSGP
ITRI
APD
CVX
CHTR
First target price reached for CHTR, selling half at market price.
Second target price reached for CHTR, selling all at market price.
DOX
NXST
First target price reached for NXST, selling half at market price.
SGEN
ADC
EA
First target price reached for EA, selling half at market price.
HOLX
MKC
HLI
First target price reached for HLI, selling half at market price.
Second target price reached for HLI, selling all at market price.
TW
ARCH
BR
First target price reached for BR, selling half at market price.
INTU
First target price reached for INTU, selling half at market price.
HUBG
First target price reached fo

ConnectionError: HTTPSConnectionPool(host='api.robinhood.com', port=443): Max retries exceeded with url: /positions/?nonzero=true (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x000001C526FE7AC0>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))